**BRONZE LAYER: UPLOAD AND INGEST DATA INTO DELTA LAKE**

List the objects inside dbfs 

In [0]:
dbutils.fs.ls("dbfs:/")

[FileInfo(path='dbfs:/FileStore/', name='FileStore/', size=0, modificationTime=1750316455000),
 FileInfo(path='dbfs:/Volume/', name='Volume/', size=0, modificationTime=0),
 FileInfo(path='dbfs:/Volumes/', name='Volumes/', size=0, modificationTime=0),
 FileInfo(path='dbfs:/databricks-datasets/', name='databricks-datasets/', size=0, modificationTime=0),
 FileInfo(path='dbfs:/databricks-results/', name='databricks-results/', size=0, modificationTime=0),
 FileInfo(path='dbfs:/volume/', name='volume/', size=0, modificationTime=0),
 FileInfo(path='dbfs:/volumes/', name='volumes/', size=0, modificationTime=0)]

Upload files on "upload data to DBFS" option. Store files in Filestore/tables

In [0]:
dbutils.fs.ls("dbfs:/FileStore/tables/")

[FileInfo(path='dbfs:/FileStore/tables/payments.csv', name='payments.csv', size=57666115, modificationTime=1750316466000),
 FileInfo(path='dbfs:/FileStore/tables/riders.csv', name='riders.csv', size=5594949, modificationTime=1750316467000),
 FileInfo(path='dbfs:/FileStore/tables/stations.csv', name='stations.csv', size=49552, modificationTime=1750316455000),
 FileInfo(path='dbfs:/FileStore/tables/trips.csv', name='trips.csv', size=440125504, modificationTime=1750316533000)]

In [0]:
df1 = spark.read.format("csv").option("header", "false").load("dbfs:/FileStore/tables/stations.csv")
df2 = spark.read.format("csv").option("header", "false").load("dbfs:/FileStore/tables/payments.csv")
df3 = spark.read.format("csv").option("header", "false").load("dbfs:/FileStore/tables/riders.csv")
df4 = spark.read.format("csv").option("header", "false").load("dbfs:/FileStore/tables/trips.csv")

csv files does not come up with headers so will be needed to put them in next stages (Silver Layer). Column names can be taken from ERD Model of Project Overview

In [0]:
display(df1.head(5))

_c0 _c1 _c2 _c3 525 Glenwood Ave & Touhy Ave 42.012701 -87.66605799999999 KA1503000012 Clark St & Lake St 41.88579466666667 -87.63110066666668 637 Wood St & Chicago Ave 41.895634 -87.672069 13216 State St & 33rd St 41.8347335 -87.6258275 18003 Fairbanks St & Superior St 41.89580766666667 -87.62025316666669

**Ingest into Bronze Layer in Delta Lake**

In [0]:
df1.write.format("delta").mode("overwrite").save("/delta/bronze_stations")
df2.write.format("delta").mode("overwrite").save("/delta/bronze_payments")
df3.write.format("delta").mode("overwrite").save("/delta/bronze_riders")
df4.write.format("delta").mode("overwrite").save("/delta/bronze_trips")

In [0]:
dbutils.fs.ls("/delta/")

[FileInfo(path='dbfs:/delta/bronze_payments/', name='bronze_payments/', size=0, modificationTime=1750323496000),
 FileInfo(path='dbfs:/delta/bronze_riders/', name='bronze_riders/', size=0, modificationTime=1750323500000),
 FileInfo(path='dbfs:/delta/bronze_stations/', name='bronze_stations/', size=0, modificationTime=1750323481000),
 FileInfo(path='dbfs:/delta/bronze_trips/', name='bronze_trips/', size=0, modificationTime=1750323502000)]

Look one file to see it is partioned and saved in parquet

In [0]:
dbutils.fs.ls("/delta/bronze_payments")

[FileInfo(path='dbfs:/delta/bronze_payments/_delta_log/', name='_delta_log/', size=0, modificationTime=1750323496000),
 FileInfo(path='dbfs:/delta/bronze_payments/part-00000-b515bc51-77a7-4a0e-8ed3-5fb0348f6d09.c000.snappy.parquet', name='part-00000-b515bc51-77a7-4a0e-8ed3-5fb0348f6d09.c000.snappy.parquet', size=2987736, modificationTime=1750323498000),
 FileInfo(path='dbfs:/delta/bronze_payments/part-00001-20a2d1ca-d90a-4faa-afce-829307b1d6f3.c000.snappy.parquet', name='part-00001-20a2d1ca-d90a-4faa-afce-829307b1d6f3.c000.snappy.parquet', size=2908142, modificationTime=1750323498000),
 FileInfo(path='dbfs:/delta/bronze_payments/part-00002-61338132-c64c-4c27-8f74-f31f8a866676.c000.snappy.parquet', name='part-00002-61338132-c64c-4c27-8f74-f31f8a866676.c000.snappy.parquet', size=2822807, modificationTime=1750323498000),
 FileInfo(path='dbfs:/delta/bronze_payments/part-00003-9b5f4099-5b85-4d29-a4cc-0defd76774c0.c000.snappy.parquet', name='part-00003-9b5f4099-5b85-4d29-a4cc-0defd76774c0.c0

**SILVER LAYER: TRANSFORM AND PROCESS RAW TABLES TO CREATE DELTA LAKE TABLES**

Analize files to do some data cleaning, like adding column names, changing data types, dropping duplicates, etc.

**Import Libraries needed**

In [0]:
from pyspark.sql.functions import col, to_date, to_timestamp
from pyspark.sql.types import BooleanType, DoubleType, DateType

**1. Stations**

In [0]:
df_stations = spark.read.format("delta").load("/delta/bronze_stations")
display(df_stations.head(5))

_c0 _c1 _c2 _c3 525 Glenwood Ave & Touhy Ave 42.012701 -87.66605799999999 KA1503000012 Clark St & Lake St 41.88579466666667 -87.63110066666668 637 Wood St & Chicago Ave 41.895634 -87.672069 13216 State St & 33rd St 41.8347335 -87.6258275 18003 Fairbanks St & Superior St 41.89580766666667 -87.62025316666669

In [0]:
df_stations = df_stations.toDF("station_id", "name", "latitude", "longitude") # Rename columns
display(df_stations.head(5))

station_id name latitude longitude 525 Glenwood Ave & Touhy Ave 42.012701 -87.66605799999999 KA1503000012 Clark St & Lake St 41.88579466666667 -87.63110066666668 637 Wood St & Chicago Ave 41.895634 -87.672069 13216 State St & 33rd St 41.8347335 -87.6258275 18003 Fairbanks St & Superior St 41.89580766666667 -87.62025316666669

In [0]:
df_stations.printSchema()

root
 |-- station_id: string (nullable = true)
 |-- name: string (nullable = true)
 |-- latitude: string (nullable = true)
 |-- longitude: string (nullable = true)



In [0]:
df_stations = df_stations.withColumn("latitude", col("latitude").cast(DoubleType())) \
           .withColumn("longitude", col("longitude").cast(DoubleType()))

In [0]:
df_stations.printSchema()

root
 |-- station_id: string (nullable = true)
 |-- name: string (nullable = true)
 |-- latitude: double (nullable = true)
 |-- longitude: double (nullable = true)



In [0]:
display(df_stations.head(5))


station_id name latitude longitude 525 Glenwood Ave & Touhy Ave 42.012701 -87.66605799999999 KA1503000012 Clark St & Lake St 41.88579466666667 -87.63110066666668 637 Wood St & Chicago Ave 41.895634 -87.672069 13216 State St & 33rd St 41.8347335 -87.6258275 18003 Fairbanks St & Superior St 41.89580766666667 -87.62025316666669

Check for duplicates, and as we can see there is None for stations_table. So there is no big data cleaning to do in this case

In [0]:
duplicates_stations = df_stations.groupBy("station_id").count().filter("count > 1")
display(duplicates_stations)

station_id count

**2. Riders**

In [0]:
df_riders = spark.read.format("delta").load("/delta/bronze_riders")
df_riders = df_riders.toDF("rider_id", "first", "last", "address", "birthday", "account_start_date", "account_end_date", "is_member") # Rename columns
display(df_riders.head(10))

rider_id first last address birthday account_start_date account_end_date is_member 1000 Diana Clark 1200 Alyssa Squares 1989-02-13 2019-04-23 null True 1001 Jennifer Smith 397 Diana Ferry 1976-08-10 2019-11-01 2020-09-01 True 1002 Karen Smith 644 Brittany Row Apt. 097 1998-08-10 2022-02-04 null True 1003 Bryan Roberts 996 Dickerson Turnpike 1999-03-29 2019-08-26 null False 1004 Jesse Middleton 7009 Nathan Expressway 1969-04-11 2019-09-14 null True 1005 Christine Rodriguez 224 Washington Mills Apt. 467 1974-08-27 2020-03-24 null False 1006 Alicia Taylor 1137 Angela Locks 2004-01-30 2020-11-27 2021-12-01 True 1007 Benjamin Fernandez 979 Phillips Ways 1988-01-11 2016-12-11 null False 1008 John Crawford 7691 Evans Court 1987-02-21 2021-03-28 2021-07-01 True 1009 Victoria Ritter 9922 Jim Crest Apt. 319 1981-02-07 2020-06-12 2021-11-01 True

In [0]:
df_riders.printSchema()

root
 |-- rider_id: string (nullable = true)
 |-- first: string (nullable = true)
 |-- last: string (nullable = true)
 |-- address: string (nullable = true)
 |-- birthday: string (nullable = true)
 |-- account_start_date: string (nullable = true)
 |-- account_end_date: string (nullable = true)
 |-- is_member: string (nullable = true)



In [0]:
df_riders = df_riders.withColumn("birthday", to_date("birthday")) \
             .withColumn("account_start_date", to_date("account_start_date")) \
             .withColumn("account_end_date", to_date("account_end_date")) \
             .withColumn("is_member", col("is_member").cast(BooleanType()))

In [0]:
df_riders.printSchema()

root
 |-- rider_id: string (nullable = true)
 |-- first: string (nullable = true)
 |-- last: string (nullable = true)
 |-- address: string (nullable = true)
 |-- birthday: date (nullable = true)
 |-- account_start_date: date (nullable = true)
 |-- account_end_date: date (nullable = true)
 |-- is_member: boolean (nullable = true)



In [0]:
duplicates_riders = df_riders.groupBy("rider_id").count().filter("count > 1")
display(duplicates_riders)

rider_id count

**3. Payments**

In [0]:
df_payments = spark.read.format("delta").load("/delta/bronze_payments")
df_payments = df_payments.toDF("payment_id", "date", "amount", "rider_id") # Rename columns
display(df_payments.head(10))

payment_id date amount rider_id 539256 2020-08-01 9.0 21826 539257 2020-09-01 9.0 21826 539258 2020-10-01 9.0 21826 539259 2020-11-01 9.0 21826 539260 2020-12-01 9.0 21826 539261 2021-01-01 9.0 21826 539262 2021-02-01 9.0 21826 539263 2021-03-01 9.0 21826 539264 2021-04-01 9.0 21826 539265 2021-05-01 9.0 21826

In [0]:
df_payments = df_payments.withColumn("date", to_date("date")) \
             .withColumn("amount", col("amount").cast(DoubleType()))
df_payments.printSchema()

root
 |-- payment_id: string (nullable = true)
 |-- date: date (nullable = true)
 |-- amount: double (nullable = true)
 |-- rider_id: string (nullable = true)



In [0]:
duplicates_payments = df_payments.groupBy("payment_id").count().filter("count > 1")
display(duplicates_payments)

payment_id count

**4. Trips**

In [0]:
df_trips = spark.read.format("delta").load("/delta/bronze_trips")
df_trips = df_trips.toDF("trip_id", "rideable_type", "started_at", "ended_at", "start_station_id", "end_station_id", "rider_id") # Rename columns
display(df_trips.head(10))

trip_id rideable_type started_at ended_at start_station_id end_station_id rider_id 222BB8E5059252D7 classic_bike 2021-06-13 09:48:47 2021-06-13 10:07:23 KA1503000064 13021 34062 1826E16CB5486018 classic_bike 2021-06-21 22:59:13 2021-06-21 23:04:29 TA1306000010 13021 5342 3D9B6A0A5330B04D classic_bike 2021-06-18 16:06:42 2021-06-18 16:12:02 TA1305000030 13021 3714 07E82F5E9C9E490F classic_bike 2021-06-17 16:46:23 2021-06-17 17:02:45 TA1305000034 13021 18793 A8E94BAECBF0C2DD docked_bike 2021-06-13 17:36:29 2021-06-13 18:30:39 TA1308000009 TA1308000009 43342 378F4AB323AA1D14 docked_bike 2021-06-13 13:20:10 2021-06-13 14:06:14 TA1308000009 TA1308000009 6693 38AD311DC2EB1FBE docked_bike 2021-06-16 17:14:30 2021-06-16 17:28:34 KA1503000019 KA1503000019 71480 1D466737F0B18097 docked_bike 2021-06-27 14:51:52 2021-06-27 15:26:39 TA1308000009 TA1308000009 50846 27E1142E1ACFAEFB electric_bike 2021-06-21 13:58:26 2021-06-21 13:58:53 13257 13257 18951 67F2A115DAE77924 classic_bike 2021-06-22 00:51:43 2021-06-22 01:08:25 TA1308000009 TA1308000009 63987

In [0]:
df_trips = df_trips.withColumn("started_at", to_timestamp("started_at")) \
             .withColumn("ended_at", to_timestamp("ended_at"))
df_trips.printSchema()

root
 |-- trip_id: string (nullable = true)
 |-- rideable_type: string (nullable = true)
 |-- started_at: timestamp (nullable = true)
 |-- ended_at: timestamp (nullable = true)
 |-- start_station_id: string (nullable = true)
 |-- end_station_id: string (nullable = true)
 |-- rider_id: string (nullable = true)



In [0]:
display(df_trips.head(10))

trip_id rideable_type started_at ended_at start_station_id end_station_id rider_id 222BB8E5059252D7 classic_bike 2021-06-13T09:48:47Z 2021-06-13T10:07:23Z KA1503000064 13021 34062 1826E16CB5486018 classic_bike 2021-06-21T22:59:13Z 2021-06-21T23:04:29Z TA1306000010 13021 5342 3D9B6A0A5330B04D classic_bike 2021-06-18T16:06:42Z 2021-06-18T16:12:02Z TA1305000030 13021 3714 07E82F5E9C9E490F classic_bike 2021-06-17T16:46:23Z 2021-06-17T17:02:45Z TA1305000034 13021 18793 A8E94BAECBF0C2DD docked_bike 2021-06-13T17:36:29Z 2021-06-13T18:30:39Z TA1308000009 TA1308000009 43342 378F4AB323AA1D14 docked_bike 2021-06-13T13:20:10Z 2021-06-13T14:06:14Z TA1308000009 TA1308000009 6693 38AD311DC2EB1FBE docked_bike 2021-06-16T17:14:30Z 2021-06-16T17:28:34Z KA1503000019 KA1503000019 71480 1D466737F0B18097 docked_bike 2021-06-27T14:51:52Z 2021-06-27T15:26:39Z TA1308000009 TA1308000009 50846 27E1142E1ACFAEFB electric_bike 2021-06-21T13:58:26Z 2021-06-21T13:58:53Z 13257 13257 18951 67F2A115DAE77924 classic_bike 2021-06-22T00:51:43Z 2021-06-22T01:08:25Z TA1308000009 TA1308000009 63987

**Export the DataFrames in Delta Lake Silver Layer using pyspark and save as Tables**

In [0]:
df_stations.write.format("delta").mode("overwrite").saveAsTable("silver_stations")
df_payments.write.format("delta").mode("overwrite").saveAsTable("silver_payments")
df_riders.write.format("delta").mode("overwrite").saveAsTable("silver_riders")
df_trips.write.format("delta").mode("overwrite").saveAsTable("silver_trips")

DataFrames were saved in Delta as tables in **hive_metastore default db** and ready to be used in Gold Layer to create fact and dimension tables

In [0]:
%sql SHOW TABLES;

database tableName isTemporary default silver_payments false default silver_riders false default silver_stations false default silver_trips false _sqldf true

**GOLDEN LAYER: CREATE TABLES IN DELTA AND MODEL FACT AND DIMENSION TABLES**

Fact Tables:

1. fact_trips
2. fact_payments

**FACT TRIPS**

In [0]:
%sql

SELECT
    t.trip_id,
    t.rideable_type,
    t.start_station_id,
    t.started_at,
    t.end_station_id,
    t.ended_at,
    t.rider_id,
    ROUND((unix_timestamp(t.ended_at) - unix_timestamp(t.started_at)) / 60.0, 2) AS trip_duration_minutes,
    FLOOR(DATEDIFF(t.started_at, r.birthday) / 365.25) AS rider_age_at_trip,
    DATE(t.started_at) AS date_id
FROM silver_trips t
JOIN silver_riders r
  ON t.rider_id = r.rider_id


trip_id rideable_type start_station_id started_at end_station_id ended_at rider_id trip_duration_minutes rider_age_at_trip date_id 222BB8E5059252D7 classic_bike KA1503000064 2021-06-13T09:48:47Z 13021 2021-06-13T10:07:23Z 34062 18.60 30 2021-06-13 1826E16CB5486018 classic_bike TA1306000010 2021-06-21T22:59:13Z 13021 2021-06-21T23:04:29Z 5342 5.27 26 2021-06-21 3D9B6A0A5330B04D classic_bike TA1305000030 2021-06-18T16:06:42Z 13021 2021-06-18T16:12:02Z 3714 5.33 26 2021-06-18 07E82F5E9C9E490F classic_bike TA1305000034 2021-06-17T16:46:23Z 13021 2021-06-17T17:02:45Z 18793 16.37 18 2021-06-17 A8E94BAECBF0C2DD docked_bike TA1308000009 2021-06-13T17:36:29Z TA1308000009 2021-06-13T18:30:39Z 43342 54.17 28 2021-06-13 378F4AB323AA1D14 docked_bike TA1308000009 2021-06-13T13:20:10Z TA1308000009 2021-06-13T14:06:14Z 6693 46.07 28 2021-06-13 38AD311DC2EB1FBE docked_bike KA1503000019 2021-06-16T17:14:30Z KA1503000019 2021-06-16T17:28:34Z 71480 14.07 56 2021-06-16 1D466737F0B18097 docked_bike TA1308000009 2021-06-27T14:51:52Z TA1308000009 2021-06-27T15:26:39Z 50846 34.78 40 2021-06-27 27E1142E1ACFAEFB electric_bike 13257 2021-06-21T13:58:26Z 13257 2021-06-21T13:58:53Z 18951 0.45 21 2021-06-21 67F2A115DAE77924 classic_bike TA1308000009 2021-06-22T00:51:43Z TA1308000009 2021-06-22T01:08:25Z 63987 16.70 37 2021-06-22 D30A0F588CAB9948 docked_bike 13036 2021-06-03T16:40:02Z 13434 2021-06-03T17:04:22Z 52600 24.33 39 2021-06-03 B6D051538810CE8A classic_bike KA1503000064 2021-06-14T19:19:04Z TA1308000009 2021-06-14T19:55:54Z 58393 36.83 21 2021-06-14 9724F787201C914E classic_bike 13042 2021-06-06T19:37:03Z 13434 2021-06-06T19:56:22Z 45636 19.32 28 2021-06-06 5C07EC15B5E1F93C classic_bike 13084 2021-06-19T20:17:01Z 13257 2021-06-19T20:27:19Z 66194 10.30 30 2021-06-19 1BFBE159F63DF1AF classic_bike KA1503000043 2021-06-30T09:06:25Z 13021 2021-06-30T09:09:11Z 18576 2.77 32 2021-06-30 C63897EB5765B1E6 classic_bike TA1306000003 2021-06-11T22:46:36Z 13021 2021-06-11T22:49:03Z 62971 2.45 39 2021-06-11 AAA3B86E0B459EBB electric_bike KA1503000043 2021-06-10T15:56:15Z 13434 2021-06-10T16:03:51Z 8235 7.60 33 2021-06-10 B22FA59E25D85FFB electric_bike 13157 2021-06-10T17:20:02Z 13021 2021-06-10T17:26:05Z 51431 6.05 46 2021-06-10 ADA725E548D6CF84 electric_bike KA1503000043 2021-06-08T16:12:24Z 13434 2021-06-08T16:19:32Z 40507 7.13 36 2021-06-08 AC061F7C81D386EE electric_bike 13016 2021-06-25T10:04:56Z 13021 2021-06-25T10:15:01Z 67393 10.08 24 2021-06-25 92AFE274FABD11CE classic_bike KA17018054 2021-06-05T12:01:26Z 13021 2021-06-05T12:17:16Z 16460 15.83 18 2021-06-05 3256D982124A51CC classic_bike 657 2021-06-04T19:00:27Z 13257 2021-06-04T19:12:47Z 75162 12.33 24 2021-06-04 F863618B48098D75 docked_bike 13059 2021-06-03T01:16:01Z 13021 2021-06-05T18:07:36Z 13478 3891.58 34 2021-06-03 71DE5B8A7F699133 classic_bike TA1307000164 2021-06-11T20:58:10Z TA1308000009 2021-06-11T21:10:53Z 62165 12.72 48 2021-06-11 F27720C77BF53D45 classic_bike TA1309000033 2021-06-02T19:00:27Z 13257 2021-06-02T19:18:29Z 72120 18.03 24 2021-06-02 70450A18BC3E1D2C electric_bike KA1503000043 2021-06-26T23:05:28Z 13434 2021-06-26T23:20:08Z 40507 14.67 36 2021-06-26 67D4F59EF1AF0860 electric_bike KA1503000043 2021-06-14T15:39:18Z 13434 2021-06-14T15:46:29Z 38429 7.18 38 2021-06-14 E3C9A476285BCAC6 classic_bike 13042 2021-06-27T12:18:43Z TA1308000009 2021-06-27T14:15:43Z 32429 117.00 20 2021-06-27 FD52122A0097A531 classic_bike WL-012 2021-06-01T16:37:20Z 13021 2021-06-01T16:39:29Z 65021 2.15 58 2021-06-01 62488E6B93B305DC classic_bike WL-012 2021-06-18T19:52:27Z 13021 2021-06-18T20:51:45Z 42347 59.30 21 2021-06-18 C2B3554CF7143205 classic_bike TA1309000029 2021-06-19T02:05:11Z 13257 2021-06-19T02:14:15Z 22598 9.07 27 2021-06-19 65DF68F8CFF425AC classic_bike TA1307000128 2021-06-09T18:30:03Z 13257 2021-06-09T19:07:43Z 54690 37.67 22 2021-06-09 0FB0BE3484716E54 classic_bike TA1305000022 2021-06-08T22:50:01Z 13021 2021-06-08T22:55:21Z 13575 5.33 38 2021-06-08 695E965A2C32C219 electric_bike 518 2021-06-

In [0]:
query = """
CREATE OR REPLACE TABLE golden_fact_trip
USING DELTA
AS
    SELECT
        t.trip_id,
        t.rideable_type,
        t.start_station_id,
        t.started_at,
        t.end_station_id,
        t.ended_at,
        t.rider_id,
        ROUND((unix_timestamp(t.ended_at) - unix_timestamp(t.started_at)) / 60.0, 2) AS trip_duration_minutes,
        FLOOR(DATEDIFF(t.started_at, r.birthday) / 365.25) AS rider_age_at_trip,
        DATE(t.started_at) AS date_id
    FROM silver_trips t
    JOIN silver_riders r
    ON t.rider_id = r.rider_id;
"""

In [0]:
spark.sql(query)
spark.sql("select * from golden_fact_trip limit 5;").show()

+----------------+-------------+----------------+-------------------+--------------+-------------------+--------+---------------------+-----------------+----------+
|         trip_id|rideable_type|start_station_id|         started_at|end_station_id|           ended_at|rider_id|trip_duration_minutes|rider_age_at_trip|   date_id|
+----------------+-------------+----------------+-------------------+--------------+-------------------+--------+---------------------+-----------------+----------+
|89E7AA6C29227EFF| classic_bike|             525|2021-02-12 16:14:56|           660|2021-02-12 16:21:43|   71934|                 6.78|               37|2021-02-12|
|0FEFDE2603568365| classic_bike|             525|2021-02-14 17:52:38|         16806|2021-02-14 18:12:09|   47854|                19.52|               38|2021-02-14|
|E6159D746B2DBB91|electric_bike|    KA1503000012|2021-02-09 19:10:18|  TA1305000029|2021-02-09 19:19:10|   70870|                 8.87|               33|2021-02-09|
|B32D3199F

**FACT PAYMENTS**

In [0]:
query_payments = """
CREATE OR REPLACE TABLE golden_fact_payments
USING DELTA
AS
    SELECT
        payment_id,
        rider_id,
        date,
        amount
    FROM silver_payments;
"""

spark.sql(query_payments)

DataFrame[num_affected_rows: bigint, num_inserted_rows: bigint]

In [0]:
%sql 
select * from golden_fact_payments limit 5

payment_id rider_id date amount 539256 21826 2020-08-01 9.0 539257 21826 2020-09-01 9.0 539258 21826 2020-10-01 9.0 539259 21826 2020-11-01 9.0 539260 21826 2020-12-01 9.0

Dimension tables: 

1. dim_riders
2. dim_stations
3. dim_date

dim_date will be created using pyspark in order to answer some business questions

**DIM RIDERS**

In [0]:
query_riders = """
CREATE OR REPLACE TABLE golden_dim_riders
USING DELTA
AS
SELECT
    rider_id,
    first,
    last,
    address,
    birthday,
    account_start_date,
    account_end_date,
    is_member
FROM silver_riders;
"""

spark.sql(query_riders)


DataFrame[num_affected_rows: bigint, num_inserted_rows: bigint]

In [0]:
query_stations = """
CREATE OR REPLACE TABLE golden_dim_stations
USING DELTA
AS
SELECT
    station_id,
    name,
    latitude,
    longitude
FROM silver_stations
"""

spark.sql(query_stations)

DataFrame[num_affected_rows: bigint, num_inserted_rows: bigint]

**DIM DATE**

Create a dim_date to answer business questions

In [0]:
from pyspark.sql.functions import year, quarter, month, dayofmonth, date_format, expr, sequence, explode

df_date = (
    spark
    .range(0, 1)  # dummy row
    .select(explode(sequence(expr("to_date('2018-01-01')"), expr("to_date('2030-12-31')"), expr("interval 1 day"))).alias("date_id"))
    .withColumn("year", year("date_id"))
    .withColumn("quarter", quarter("date_id"))
    .withColumn("month", month("date_id"))
    .withColumn("day", dayofmonth("date_id"))
    .withColumn("day_of_week", date_format("date_id", "EEEE"))
    .withColumn("is_weekend", expr("date_format(date_id, 'E') in ('Sat', 'Sun')"))
)

df_date.write.format("delta").mode("overwrite").saveAsTable("golden_dim_date")

In [0]:
%sql select * from golden_dim_date limit 10;

date_id year quarter month day day_of_week is_weekend 2018-01-01 2018 1 1 1 Monday false 2018-01-02 2018 1 1 2 Tuesday false 2018-01-03 2018 1 1 3 Wednesday false 2018-01-04 2018 1 1 4 Thursday false 2018-01-05 2018 1 1 5 Friday false 2018-01-06 2018 1 1 6 Saturday true 2018-01-07 2018 1 1 7 Sunday true 2018-01-08 2018 1 1 8 Monday false 2018-01-09 2018 1 1 9 Tuesday false 2018-01-10 2018 1 1 10 Wednesday false

All golden and already ready-to-user modelled tables are in the default database

In [0]:
%sql SHOW TABLES;

database tableName isTemporary default golden_dim_date false default golden_dim_riders false default golden_dim_stations false default golden_fact_payments false default golden_fact_trip false default silver_payments false default silver_riders false default silver_stations false default silver_trips false _sqldf true

**ANSWER BUSINESS QUESTIONS AFTER MODELLING DATA**

1. Analyze how much time is spent per ride

Based on date and time factors such as day of week and time of day

In [0]:
%sql
SELECT 
    d.day_of_week,
    HOUR(t.started_at) AS hour_of_day,
    SUM(t.trip_duration_minutes) AS total_duration_mins
FROM golden_fact_trip t
JOIN golden_dim_date d ON t.date_id = d.date_id
GROUP BY d.day_of_week, hour_of_day
ORDER BY d.day_of_week, hour_of_day;

day_of_week hour_of_day total_duration_mins Friday 0 189159.64 Friday 1 153622.08 Friday 2 96491.62 Friday 3 37607.67 Friday 4 38883.58 Friday 5 59033.17 Friday 6 171704.87 Friday 7 311570.83 Friday 8 401821.37 Friday 9 373118.38 Friday 10 497561.37 Friday 11 644406.82 Friday 12 799780.59 Friday 13 902952.72 Friday 14 921575.00 Friday 15 989487.00 Friday 16 1134724.04 Friday 17 1418664.62 Friday 18 1197704.00 Friday 19 896255.80 Friday 20 704904.42 Friday 21 561507.34 Friday 22 573359.69 Friday 23 518964.17 Monday 0 217491.77 Monday 1 144311.26 Monday 2 60214.36 Monday 3 54525.24 Monday 4 36253.99 Monday 5 68704.37 Monday 6 193504.36 Monday 7 343933.53 Monday 8 414387.60 Monday 9 355019.24 Monday 10 454566.81 Monday 11 647438.21 Monday 12 734470.34 Monday 13 785817.41 Monday 14 850893.89 Monday 15 835491.20 Monday 16 1058546.23 Monday 17 1293641.97 Monday 18 1085656.34 Monday 19 766619.41 Monday 20 578503.99 Monday 21 412572.27 Monday 22 308370.97 Monday 23 180037.90 Saturday 0 468490.50 Saturday 1 386400.47 Saturday 2 310464.24 Saturday 3 128348.90 Saturday 4 154416.92 Saturday 5 57846.45 Saturday 6 120978.76 Saturday 7 201063.67 Saturday 8 388681.27 Saturday 9 701982.63 Saturday 10 1100895.25 Saturday 11 1454648.92 Saturday 12 1723416.93 Saturday 13 1846070.43 Saturday 14 1825183.16 Saturday 15 1774432.58 Saturday 16 1614716.95 Saturday 17 1442642.71 Saturday 18 1458273.85 Saturday 19 1094866.63 Saturday 20 873465.96 Saturday 21 823738.67 Saturday 22 836557.14 Saturday 23 756385.44 Sunday 0 571476.77 Sunday 1 551607.41 Sunday 2 357620.01 Sunday 3 233787.39 Sunday 4 106024.15 Sunday 5 77991.44 Sunday 6 125794.96 Sunday 7 238914.98 Sunday 8 360691.59 Sunday 9 653192.04 Sunday 10 1091149.91 Sunday 11 1388737.17 Sunday 12 1534770.24 Sunday 13 1713586.70 Sunday 14 1787046.69 Sunday 15 1788918.68 Sunday 16 1671213.15 Sunday 17 1532797.64 Sunday 18 1241755.47 Sunday 19 930919.50 Sunday 20 641887.43 Sunday 21 525476.52 Sunday 22 413710.89 Sunday 23 314802.12 Thursday 0 107526.83 Thursday 1 65387.61 Thursday 2 54244.35 Thursday 3 15824.15 Thursday 4 17388.63 Thursday 5 63703.01 Thursday 6 199039.01 Thursday 7 358075.11 Thursday 8 417588.48 Thursday 9 317257.50 Thursday 10 389527.42 Thursday 11 472630.84 Thursday 12 572178.36 Thursday 13 534134.40 Thursday 14 573238.15 Thursday 15 743093.57 Thursday 16 886573.87 Thursday 17 1221115.83 Thursday 18 1138907.32 Thursday 19 918268.94 Thursday 20 608081.10 Thursday 21 516900.29 Thursday 22 453008.86 Thursday 23 270548.19 Tuesday 0 92761.87 Tuesday 1 53022.33 Tuesday 2 47573.60 Tuesday 3 31298.80 Tuesday 4 25484.47 Tuesday 5 86578.56 Tuesday 6 213417.61 Tuesday 7 437873.21 Tuesday 8 478875.63 Tuesday 9 343719.99 Tuesday 10 378754.27 Tuesday 11 459826.73 Tuesday 12 565188.70 Tuesday 13 621118.09 Tuesday 14 597896.25 Tuesday 15 708288.96 Tuesday 16 982197.90 Tuesday 17 1373485.87 Tuesday 18 1162109.46 Tuesday 19 813858.80 Tuesday 20 538955.92 Tuesday 21 395533.84 Tuesday 22 345744.25 Tuesday 23 239317.93 Wednesday 0 126594.42 Wednesday 1 63227.63 Wednesday 2 42167.09 Wednesday 3 27755.63 Wednesday 4 16585.77 Wednesday 5 73743.67 Wednesday 6 205053.57 Wednesday 7 418791.79 Wednesday 8 489098.00 Wednesday 9 371430.90 Wednesday 10 363335.00 Wednesday 11 466533.19 Wednesday 12 575471.14 Wednesday 13 567946.11 Wednesday 14 608068.27 Wednesday 15 759320.72 Wednesday 16 957684.50 Wednesday 17 1326184.21 Wednesday 18 1117695.19 Wednesday 19 885749.73 Wednesday 20 615883.08 Wednesday 21 443285.10 Wednesday 22 331948.95 Wednesday 23 262320.05

- Based on which station is the starting and / or ending station


In [0]:
%sql
SELECT 
    s.name AS start_station_name,
    SUM(t.trip_duration_minutes) AS total_duration_mins
FROM golden_fact_trip t
JOIN golden_dim_stations s ON t.start_station_id = s.station_id
GROUP BY s.name
ORDER BY total_duration_mins DESC;

start_station_name total_duration_mins Streeter Dr & Grand Ave 3131935.61 Millennium Park 1955578.36 Lake Shore Dr & Monroe St 1782985.48 Michigan Ave & Oak St 1551938.82 Lake Shore Dr & North Blvd 1353331.03 Theater on the Lake 1044941.95 Shedd Aquarium 1001701.84 Dusable Harbor 947083.28 Wabash Ave & Grand Ave 890235.85 Indiana Ave & Roosevelt Rd 886862.72 Lake Shore Dr & Ohio St 842971.38 Michigan Ave & Lake St 806794.71 Michigan Ave & Washington St 802872.09 Buckingham Fountain 714221.58 New St & Illinois St 703640.67 Michigan Ave & 8th St 693241.08 Clark St & Elm St 686051.93 St. Clair St & Erie St 678278.70 Montrose Harbor 671219.00 Fairbanks Ct & Grand Ave 661391.99 Wells St & Concord Ln 659284.11 Clark St & Lincoln Ave 632543.90 Clark St & Armitage Ave 599959.44 Columbus Dr & Randolph St 594902.09 Wabash Ave & Wacker Pl 572902.73 Wabash Ave & Roosevelt Rd 557397.34 Adler Planetarium 550108.76 Lake Shore Dr & Diversey Pkwy 547921.59 Lakefront Trail & Bryn Mawr Ave 547465.99 Lake Shore Dr & Belmont Ave 547093.66 Dearborn St & Erie St 542618.93 Fort Dearborn Dr & 31st St 535383.29 State St & Kinzie St 517651.53 Broadway & Barry Ave 508484.92 Lakeview Ave & Fullerton Pkwy 506384.50 Lake Shore Dr & Wellington Ave 505502.52 Michigan Ave & Jackson Blvd 500260.50 Wells St & Elm St 499983.43 State St & Randolph St 489554.74 McClurg Ct & Erie St 477425.85 Wilton Ave & Belmont Ave 473906.71 LaSalle St & Illinois St 467976.13 Lincoln Park Conservatory 454472.22 Larrabee St & Webster Ave 441490.62 Rush St & Superior St 440393.46 Mies van der Rohe Way & Chestnut St 438866.03 Burnham Harbor 427545.58 Shore Dr & 55th St 426814.50 Clark St & Lake St 424261.83 Clark St & Wrightwood Ave 418269.87 Wabash Ave & 9th St 417362.67 Michigan Ave & Pearson St 417297.48 Pine Grove Ave & Waveland Ave 416276.04 Stockton Dr & Wrightwood Ave 414958.33 Green St & Madison St 408219.87 Sheffield Ave & Waveland Ave 404760.46 Dearborn Pkwy & Delaware Pl 404439.84 Clark St & Newport St 400953.80 Rush St & Cedar St 399829.94 Wells St & Huron St 395972.84 Wells St & Evergreen Ave 391722.93 Ashland Ave & Division St 389916.41 Kingsbury St & Kinzie St 385063.99 Clark St & Drummond Pl 380997.87 Halsted St & Roscoe St 380274.94 Lincoln Ave & Fullerton Ave 375613.58 Mies van der Rohe Way & Chicago Ave 373856.61 Broadway & Cornelia Ave 372716.44 Wells St & Hubbard St 369224.74 Damen Ave & Pierce Ave 368578.50 Clark St & Schiller St 367063.49 Clinton St & Madison St 362635.74 Green St & Randolph St 358507.38 Kedzie Ave & Milwaukee Ave 358130.75 Field Blvd & South Water St 355070.62 Federal St & Polk St 348686.54 Wabash Ave & Adams St 347403.37 Franklin St & Jackson Blvd 337705.92 Cityfront Plaza Dr & Pioneer Ct 337236.51 Broadway & Waveland Ave 336458.16 Morgan St & Lake St 335041.39 Michigan Ave & Madison St 332634.66 Southport Ave & Roscoe St 331356.42 Broadway & Belmont Ave 330449.33 Clark St & North Ave 327347.99 Cannon Dr & Fullerton Ave 327301.53 Desplaines St & Kinzie St 326270.69 Dearborn St & Monroe St 325975.30 Canal St & Adams St 317002.17 Lakefront Trail & Wilson Ave 310834.80 Daley Center Plaza 309063.35 Clark St & Wellington Ave 309011.46 Clark St & Randolph St 306758.15 Clark St & Grace St 298365.35 Michigan Ave & 14th St 297105.66 Ritchie Ct & Banks St 297090.86 Michigan Ave & Ida B Wells Dr 296658.61 Stetson Ave & South Water St 295081.58 Wood St & Milwaukee Ave 292647.70 Bissell St & Armitage Ave 290634.70 Clinton St & Washington Blvd 281924.24 Southport Ave & Waveland Ave 281767.83 Field Museum 281028.34 Halsted St & Wrightwood Ave 278831.84 Halsted St & Dickens Ave 278754.64 Pine Grove Ave & Irving Park Rd 277960.18 Milwaukee Ave & Grand Ave 277661.26 Franklin St & Chicago Ave 277085.85 Sedgwick St & North Ave 275994.75 Halsted St & Clybourn Ave 274403.62 Sheffield Ave & Wellington Ave 268095.80 Wilton Ave & Diversey Pkwy 266224.33 Wentworth Ave & Cermak Rd 263325.36 State St & Van Buren St 263155.61 Fairbanks St & Superior St 262350.38 LaSalle 

Based on age of the rider at time of the ride

In [0]:
%sql
SELECT 
    rider_age_at_trip,
    SUM(trip_duration_minutes) AS total_duration_mins
FROM golden_fact_trip
GROUP BY rider_age_at_trip
ORDER BY rider_age_at_trip;

rider_age_at_trip total_duration_mins 14 130.13 15 1616842.49 16 2785914.34 17 3011015.09 18 2613923.08 19 3042454.96 20 3237526.16 21 3187474.99 22 3272639.06 23 3341414.03 24 3348527.40 25 3533258.52 26 3583705.23 27 3362881.47 28 3455310.85 29 3383115.91 30 3611315.65 31 3176134.99 32 2954596.58 33 3149925.56 34 3168904.46 35 3006558.18 36 2703939.04 37 2706917.46 38 2693079.72 39 2534005.03 40 2325569.52 41 2024781.70 42 1715949.65 43 1715553.39 44 1640839.83 45 1441450.87 46 1508200.94 47 1047106.47 48 1038270.92 49 1150546.47 50 966304.97 51 788139.69 52 765678.00 53 630586.46 54 551800.48 55 557958.81 56 619121.81 57 449013.82 58 378543.47 59 352309.84 60 278528.28 61 204640.29 62 215701.62 63 215267.54 64 149882.94 65 148130.35 66 160924.87 67 124608.92 68 46973.20 69 54851.80 70 24564.69 71 47172.27 72 17494.36 73 22688.06 74 33693.29 75 2313.33

Based on whether the rider is a member or a casual rider

In [0]:
%sql
SELECT 
    CASE WHEN r.is_member THEN 'Member' ELSE 'Casual' END as member_type,
    SUM(t.trip_duration_minutes) AS total_duration_mins
FROM golden_fact_trip t
JOIN golden_dim_riders r ON t.rider_id = r.rider_id
GROUP BY r.is_member;

member_type total_duration_mins Member 80308322.90 Casual 19588350.40

2. Analyze how much money is spent

Per month, quarter, year

In [0]:
%sql
SELECT 
    d.year,
    d.quarter,
    d.month,
    SUM(p.amount) AS total_amount
FROM golden_fact_payments p
JOIN golden_dim_date d ON p.date = d.date_id
GROUP BY d.year, d.quarter, d.month
ORDER BY d.year, d.quarter, d.month;

year quarter month total_amount 2018 1 1 137418.30000000008 2018 1 2 142420.53999999992 2018 1 3 147189.96999999997 2018 2 4 152000.09000000003 2018 2 5 158103.36 2018 2 6 163802.63999999993 2018 3 7 167911.17000000004 2018 3 8 175022.62999999995 2018 3 9 179484.00999999995 2018 4 10 186141.85000000006 2018 4 11 191941.43000000017 2018 4 12 198669.51 2019 1 1 206395.33999999997 2019 1 2 213286.69999999995 2019 1 3 219597.40999999997 2019 2 4 227701.01000000015 2019 2 5 234522.3600000001 2019 2 6 243091.5000000003 2019 3 7 251532.5300000001 2019 3 8 258662.85999999993 2019 3 9 268256.09 2019 4 10 276125.49000000005 2019 4 11 285230.12 2019 4 12 294257.37999999983 2020 1 1 303771.75999999995 2020 1 2 313517.49999999994 2020 1 3 322366.36999999976 2020 2 4 332073.88999999984 2020 2 5 341008.2700000002 2020 2 6 351315.21000000037 2020 3 7 362433.4899999994 2020 3 8 374396.5499999999 2020 3 9 385576.3400000005 2020 4 10 398365.0299999998 2020 4 11 409920.4400000002 2020 4 12 420704.5499999996 2021 1 1 434891.0599999997 2021 1 2 447430.3699999997 2021 1 3 458784.17000000004 2021 2 4 471751.65999999945 2021 2 5 485719.2500000001 2021 2 6 500206.6500000005 2021 3 7 513013.67000000016 2021 3 8 527280.7599999998 2021 3 9 540993.5299999994 2021 4 10 555656.6 2021 4 11 566140.6100000006 2021 4 12 579229.92 2022 1 1 590499.1800000003 2022 1 2 599471.27

Per member, based on the age of the rider at account start

In [0]:
%sql
SELECT 
    r.rider_id,
    r.is_member,
    FLOOR(months_between(r.account_start_date, r.birthday) / 12) AS age_at_account_start,
    SUM(p.amount) AS total_amount
FROM golden_fact_payments p
JOIN golden_dim_riders r ON p.rider_id = r.rider_id
GROUP BY r.rider_id, r.is_member, age_at_account_start
ORDER BY total_amount DESC;

rider_id is_member age_at_account_start total_amount 65089 false 27 1658.8299999999995 63569 false 14 1608.2999999999997 11368 false 10 1600.8999999999999 19270 false 30 1594.4699999999996 39136 false 11 1586.0099999999986 51831 false 35 1584.7500000000002 38365 false 42 1580.88 7243 false 19 1571.3000000000002 20017 false 8 1568.9899999999996 60682 false 24 1567.5500000000006 7555 false 46 1563.45 51610 false 19 1557.4699999999996 14523 false 15 1556.3999999999994 65498 false 14 1556.1399999999994 7254 false 12 1554.1200000000006 18292 false 27 1549.7299999999996 48580 false 9 1548.6499999999996 24070 false 28 1545.0200000000004 14319 false 44 1543.2600000000002 16462 false 21 1540.73 65138 false 17 1536.2300000000012 38813 false 13 1535.8699999999992 24873 false 10 1534.5199999999998 22158 false 8 1530.4499999999994 1101 false 29 1530.2000000000003 33267 false 17 1528.0100000000004 46990 false 49 1526.7399999999993 35401 false 15 1524.2 28624 false 43 1519.7299999999993 49163 false 27 1517.7700000000002 26204 false 34 1516.3399999999995 31578 false 8 1515.5300000000002 43719 false 14 1511.4900000000002 30419 false 31 1510.4099999999999 31552 false 16 1508.16 75860 false 30 1507.2500000000005 3113 false 44 1507.1899999999987 25353 false 51 1506.1000000000004 6625 false 9 1504.2100000000005 22100 false 11 1503.81 62729 false 32 1503.6799999999992 59759 false 32 1502.53 29504 false 21 1502.0499999999997 58332 false 16 1500.6900000000003 51713 false 16 1500.6099999999997 7074 false 26 1498.4199999999992 56504 false 15 1498.13 17404 false 32 1495.7899999999997 36295 false 24 1494.5699999999988 40202 false 22 1493.9000000000003 8540 false 12 1492.6400000000003 65663 false 8 1489.6799999999998 68837 false 7 1487.96 70965 false 7 1486.39 1098 false 37 1484.51 68062 false 19 1484.38 69644 false 16 1481.4700000000005 67723 false 24 1479.9099999999994 42322 false 34 1479.4999999999998 3793 false 23 1478.9900000000007 55485 false 55 1477.6599999999999 22755 false 23 1476.4999999999995 21034 false 25 1475.81 18824 false 10 1474.5699999999995 58012 false 36 1473.5300000000004 51176 false 13 1472.6099999999997 25723 false 24 1471.9599999999996 7222 false 19 1471.7699999999995 4834 false 12 1470.6500000000003 71332 false 35 1469.3100000000004 28750 false 37 1467.920000000001 49883 false 25 1466.7499999999995 73973 false 32 1465.2999999999997 21198 false 25 1464.9500000000007 40161 false 20 1464.65 2260 false 45 1461.5200000000011 61085 false 12 1460.9700000000005 35940 false 38 1459.0900000000001 21785 false 41 1458.9000000000003 47295 false 14 1458.7299999999996 36469 false 19 1458.2700000000002 56437 false 13 1457.4000000000003 21599 false 7 1456.45 32634 false 11 1455.8700000000003 3154 false 23 1455.39 61559 false 25 1455.1400000000003 29744 false 17 1453.4999999999998 60943 false 31 1453.3899999999999 36150 false 18 1452.4699999999998 50845 false 33 1452.3300000000002 7967 false 14 1451.789999999999 69594 false 15 1451.5800000000002 7063 false 13 1451.0900000000006 55926 false 10 1448.1100000000004 48546 false 15 1447.9800000000002 8657 false 16 1445.7100000000003 17905 false 50 1445.7000000000003 26182 false 23 1444.8900000000006 73024 false 12 1444.8000000000004 49813 false 26 1442.3300000000008 75178 false 16 1442.2199999999998 13993 false 30 1441.85 10648 false 8 1441.5699999999997 54127 false 10 1441.4899999999996 16400 false 44 1440.6499999999999 26210 false 13 1439.5800000000002 26571 false 54 1439.53 2502 false 18 1439.5200000000002 23351 false 23 1438.47 31460 false 14 1437.9999999999989 50051 false 12 1436.1999999999998 64075 false 11 1435.6499999999999 13834 false 8 1432.4400000000003 58065 false 29 1432.43 73541 false 29 1430.7700000000004 74390 false 39 1430.2299999999996 73276 false 37 1429.8499999999997 65543 false 30 1427.5500000000002 65996 false 12 1427.1200000000001 18899 false 8 1426.650000000001 16984 false 19 1426.4699999999993 1072 false 19 1424.74 19663 false 33 1424.74 41814 false 11 1424.5699999999995 4151 fal

In [0]:
%sql
select * from golden_dim_riders where rider_id = 68837;

rider_id first last address birthday account_start_date account_end_date is_member 68837 Cassidy Camacho 2695 Simpson Squares 2005-11-26 2013-05-15 null false

3. EXTRA CREDIT - Analyze how much money is spent per member

Based on how many rides the rider averages per month

In [0]:
%sql
WITH rides_per_month AS (
    SELECT 
        rider_id,
        YEAR(started_at) AS year,
        MONTH(started_at) AS month,
        COUNT(*) AS total_rides
    FROM golden_fact_trip
    GROUP BY rider_id, year, month
),
rides_avg AS (
    SELECT 
        rider_id,
        AVG(total_rides) AS avg_monthly_rides
    FROM rides_per_month
    GROUP BY rider_id
)
SELECT 
    r.rider_id,
    r.is_member,
    rides_avg.avg_monthly_rides,
    SUM(p.amount) AS total_amount
FROM golden_fact_payments p
JOIN golden_dim_riders r ON p.rider_id = r.rider_id --and r.is_member = true
JOIN rides_avg ON r.rider_id = rides_avg.rider_id
GROUP BY r.rider_id, r.is_member, rides_avg.avg_monthly_rides
ORDER BY total_amount DESC;


rider_id is_member avg_monthly_rides total_amount 65089 false 34.083333333333336 1658.8299999999995 11368 false 3.1666666666666665 1600.8999999999999 19270 false 56.166666666666664 1594.4699999999996 51831 false 1.0 1584.7500000000002 38365 false 14.833333333333334 1580.88 51610 false 1.0 1557.4699999999996 14523 false 1.6666666666666667 1556.3999999999994 14319 false 25.272727272727273 1543.2600000000002 16462 false 3.25 1540.73 38813 false 3.0 1535.8699999999992 24873 false 12.545454545454545 1534.5199999999998 33267 false 28.818181818181817 1528.0100000000004 46990 false 1.375 1526.7399999999993 35401 false 3.4 1524.2 28624 false 2.0 1519.7299999999993 43719 false 22.363636363636363 1511.4900000000002 30419 false 3.111111111111111 1510.4099999999999 31552 false 23.5 1508.16 75860 false 4.833333333333333 1507.2500000000005 22100 false 5.636363636363637 1503.81 62729 false 19.454545454545453 1503.6799999999992 59759 false 1.0 1502.53 29504 false 1.0 1502.0499999999997 51713 false 1.6666666666666667 1500.6099999999997 36295 false 1.5 1494.5699999999988 8540 false 1.75 1492.6400000000003 67723 false 1.75 1479.9099999999994 42322 false 24.833333333333332 1479.4999999999998 55485 false 1.0 1477.6599999999999 58012 false 13.0 1473.5300000000004 51176 false 1.0 1472.6099999999997 7222 false 9.818181818181818 1471.7699999999995 28750 false 31.5 1467.920000000001 21198 false 22.583333333333332 1464.9500000000007 40161 false 25.666666666666668 1464.65 2260 false 1.8571428571428572 1461.5200000000011 21785 false 5.2727272727272725 1458.9000000000003 47295 false 1.3333333333333333 1458.7299999999996 36469 false 11.0 1458.2700000000002 56437 false 2.0 1457.4000000000003 21599 false 5.2 1456.45 32634 false 6.583333333333333 1455.8700000000003 61559 false 1.0 1455.1400000000003 29744 false 18.666666666666668 1453.4999999999998 50845 false 23.166666666666668 1452.3300000000002 7967 false 3.857142857142857 1451.789999999999 69594 false 1.0 1451.5800000000002 55926 false 37.0 1448.1100000000004 8657 false 9.9 1445.7100000000003 17905 false 6.2727272727272725 1445.7000000000003 26182 false 13.25 1444.8900000000006 73024 false 4.818181818181818 1444.8000000000004 75178 false 8.454545454545455 1442.2199999999998 13993 false 2.9 1441.85 10648 false 2.0 1441.5699999999997 26571 false 1.0 1439.53 50051 false 10.4 1436.1999999999998 73541 false 4.363636363636363 1430.7700000000004 73276 false 31.916666666666668 1429.8499999999997 65996 false 10.083333333333334 1427.1200000000001 18899 false 1.5 1426.650000000001 9921 false 8.5 1420.3200000000002 24595 false 2.875 1419.69 12104 false 3.3 1419.1600000000005 23537 false 12.416666666666666 1417.5599999999997 9454 false 3.0 1416.8300000000004 10631 false 14.416666666666666 1416.3700000000006 63944 false 7.083333333333333 1414.4900000000002 7931 false 5.583333333333333 1413.8999999999999 64030 false 5.4 1413.1 23434 false 2.0 1411.1600000000003 37660 false 9.083333333333334 1410.8500000000004 37516 false 6.636363636363637 1407.8900000000003 32003 false 5.818181818181818 1407.5599999999995 47120 false 21.454545454545453 1407.48 13787 false 1.0 1405.8600000000006 51442 false 5.6 1403.67 65357 false 22.833333333333332 1402.4700000000012 28887 false 2.0 1400.2700000000002 52919 false 1.0 1399.67 40425 false 18.083333333333332 1396.8499999999997 36051 false 1.75 1393.9199999999996 20592 false 3.0 1392.9399999999994 34366 false 1.6 1392.1400000000006 67899 false 1.8 1392.0699999999995 4206 false 1.6666666666666667 1390.1400000000003 43420 false 2.4 1386.3300000000004 47243 false 30.333333333333332 1381.35 58838 false 13.363636363636363 1380.14 41334 false 1.5 1379.5200000000004 65495 false 1.0 1379.4200000000005 66671 false 4.583333333333333 1379.0500000000002 41045 false 2.888888888888889 1376.5199999999995 12337 false 7.666666666666667 1375.83 39508 false 7.25 1374.3099999999997 7878 false 3.5454545454545454 1373.4900000000002 46694 false 14.75 1370.4099999999999 5836 false 44.083333333333336 1369.25000000000

Based on how many minutes the rider spends on a bike per month

In [0]:
%sql
WITH minutes_per_month AS (
    SELECT 
        rider_id,
        YEAR(started_at) AS year,
        MONTH(started_at) AS month,
        SUM(trip_duration_minutes) AS total_minutes
    FROM golden_fact_trip
    GROUP BY rider_id, year, month
),
minutes_avg AS (
    SELECT 
        rider_id,
        AVG(total_minutes) AS avg_monthly_minutes
    FROM minutes_per_month
    GROUP BY rider_id
)
SELECT 
    r.rider_id,
    r.is_member,
    minutes_avg.avg_monthly_minutes,
    SUM(p.amount) AS total_amount
FROM golden_fact_payments p
JOIN golden_dim_riders r ON p.rider_id = r.rider_id
JOIN minutes_avg ON r.rider_id = minutes_avg.rider_id
GROUP BY r.rider_id, r.is_member, minutes_avg.avg_monthly_minutes
ORDER BY total_amount DESC;


rider_id is_member avg_monthly_minutes total_amount 65089 false 854.117500 1658.8299999999995 11368 false 55.762500 1600.8999999999999 19270 false 788.572500 1594.4699999999996 51831 false 23.270000 1584.7500000000002 38365 false 425.622500 1580.88 51610 false 19.860000 1557.4699999999996 14523 false 95.530000 1556.3999999999994 14319 false 413.935455 1543.2600000000002 16462 false 122.792500 1540.73 38813 false 55.077500 1535.8699999999992 24873 false 222.458182 1534.5199999999998 33267 false 804.470000 1528.0100000000004 46990 false 30.463750 1526.7399999999993 35401 false 106.581000 1524.2 28624 false 43.907500 1519.7299999999993 43719 false 336.899091 1511.4900000000002 30419 false 63.633333 1510.4099999999999 31552 false 380.135000 1508.16 75860 false 67.864167 1507.2500000000005 22100 false 100.262727 1503.81 62729 false 308.800000 1503.6799999999992 59759 false 0.370000 1502.53 29504 false 6.530000 1502.0499999999997 51713 false 22.470000 1500.6099999999997 36295 false 29.340000 1494.5699999999988 8540 false 25.772500 1492.6400000000003 67723 false 32.525000 1479.9099999999994 42322 false 433.800833 1479.4999999999998 55485 false 10.570000 1477.6599999999999 58012 false 165.438182 1473.5300000000004 51176 false 22.780000 1472.6099999999997 7222 false 171.955455 1471.7699999999995 28750 false 446.403333 1467.920000000001 21198 false 415.394167 1464.9500000000007 40161 false 538.306667 1464.65 2260 false 50.427143 1461.5200000000011 21785 false 87.853636 1458.9000000000003 47295 false 128.083333 1458.7299999999996 36469 false 178.340833 1458.2700000000002 56437 false 103.248000 1457.4000000000003 21599 false 68.132000 1456.45 32634 false 110.844167 1455.8700000000003 61559 false 27.166667 1455.1400000000003 29744 false 626.825833 1453.4999999999998 50845 false 405.859167 1452.3300000000002 7967 false 131.958571 1451.789999999999 69594 false 39.340000 1451.5800000000002 55926 false 1083.565455 1448.1100000000004 8657 false 163.342000 1445.7100000000003 17905 false 75.062727 1445.7000000000003 26182 false 161.120833 1444.8900000000006 73024 false 68.417273 1444.8000000000004 75178 false 109.494545 1442.2199999999998 13993 false 100.924000 1441.85 10648 false 39.203750 1441.5699999999997 26571 false 12.975000 1439.53 50051 false 191.715000 1436.1999999999998 73541 false 70.317273 1430.7700000000004 73276 false 509.125000 1429.8499999999997 65996 false 226.993333 1427.1200000000001 18899 false 52.275000 1426.650000000001 9921 false 132.599167 1420.3200000000002 24595 false 102.065000 1419.69 12104 false 77.848000 1419.1600000000005 23537 false 280.760000 1417.5599999999997 9454 false 75.327143 1416.8300000000004 10631 false 257.939167 1416.3700000000006 63944 false 87.362500 1414.4900000000002 7931 false 70.412500 1413.8999999999999 64030 false 100.024000 1413.1 23434 false 39.386667 1411.1600000000003 37660 false 168.220833 1410.8500000000004 37516 false 80.289091 1407.8900000000003 32003 false 118.376364 1407.5599999999995 47120 false 774.925455 1407.48 13787 false 7.620000 1405.8600000000006 51442 false 320.335000 1403.67 65357 false 750.360833 1402.4700000000012 28887 false 61.785000 1400.2700000000002 52919 false 23.275000 1399.67 40425 false 274.834167 1396.8499999999997 36051 false 23.342500 1393.9199999999996 20592 false 76.276250 1392.9399999999994 34366 false 43.002000 1392.1400000000006 67899 false 54.490000 1392.0699999999995 4206 false 27.618333 1390.1400000000003 43420 false 47.402000 1386.3300000000004 47243 false 763.255000 1381.35 58838 false 165.287273 1380.14 41334 false 18.822500 1379.5200000000004 65495 false 32.270000 1379.4200000000005 66671 false 53.581667 1379.0500000000002 41045 false 36.948889 1376.5199999999995 12337 false 78.804167 1375.83 39508 false 122.327500 1374.3099999999997 7878 false 57.654545 1373.4900000000002 46694 false 293.193333 1370.4099999999999 5836 false 645.461667 1369.2500000000007 23076 false 8.000000 1366.2000000000003 54505 false 242.730833 1365.46 2657 false 259.655000 1363